Connecting to the Silver container to retrieve the Cleaned data

In [0]:
dbutils.fs.ls("/mnt/silver")

[FileInfo(path='dbfs:/mnt/silver/df_customer/', name='df_customer/', size=0, modificationTime=1714712773000),
 FileInfo(path='dbfs:/mnt/silver/df_product/', name='df_product/', size=0, modificationTime=1714712776000),
 FileInfo(path='dbfs:/mnt/silver/df_store/', name='df_store/', size=0, modificationTime=1714712778000)]

Checking for data in Gold container

In [0]:
dbutils.fs.ls("/mnt/gold")

[]

Assigning paths of customer, product, store tables

In [0]:
customers_path = '/mnt/silver/df_customer/'
products_path = '/mnt/silver/df_product/'
store_path = '/mnt/silver/df_store/'

Loading Data into DataFrame from delta

In [0]:
new_df_customer = spark.read.format('delta').load(customers_path)
new_df_product = spark.read.format('delta').load(products_path)
new_df_store = spark.read.format('delta').load(store_path)

Understanding data in each table

In [0]:
display(new_df_customer.head(5))

Customer_ID Customer_Name Segment Country City State Postal_Code Region Age CG/12520 Claire Gute Consumer United States Henderson Kentucky 42420 South 42 DV/13045 Darrin Van Huff Corporate United States Los Angeles California 90036 West 47 SO/20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South 19 BH/11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West 39 AA/10480 Andrew Allen Consumer United States Concord North Carolina 28027 South 31

In [0]:
display(new_df_product.head(5))

Product_ID Category Sub_Category Product_Name FUR-BO-10001798 Furniture Bookcases Bush Somerset Collection Bookcase FUR-CH-10000454 Furniture Chairs Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back OFF-LA-10000240 Office Supplies Labels Self-Adhesive Address Labels for Typewriters by Universal FUR-TA-10000577 Furniture Tables Bretford CR4500 Series Slim Rectangular Table OFF-ST-10000760 Office Supplies Storage Eldon Fold 'N Roll Cart System

In [0]:
display(new_df_store.head(5))

Order_ID Order_Date Ship_Date Ship_Mode Customer_ID Product_ID Sales Discount CA-2017-152156 2017-11-08 2017-11-11 Second Class CG/12520 FUR-BO-10001798 3929400.0 0.02 CA-2017-152156 2017-11-08 2017-11-11 Second Class CG/12520 FUR-CH-10000454 1.09791E7 0.01 CA-2017-138688 2017-06-12 2017-06-16 Second Class DV/13045 OFF-LA-10000240 219300.0 0.01 US-2016-108966 2016-10-11 2016-10-18 Standard Class SO/20335 FUR-TA-10000577 1.43636625E7 0.02 US-2016-108966 2016-10-11 2016-10-18 Standard Class SO/20335 OFF-ST-10000760 335520.0 0.03

Normalizing Product Table

In [0]:
new_df_product.select("Category", "Sub_Category").distinct().count()

17

In [0]:
new_df_product.select("Category", "Sub_Category").distinct().show()

+---------------+------------+
|       Category|Sub_Category|
+---------------+------------+
|Office Supplies|  Appliances|
|Office Supplies|   Envelopes|
|      Furniture|      Chairs|
|Office Supplies|     Storage|
|Office Supplies|       Paper|
|Office Supplies|    Supplies|
|     Technology|     Copiers|
|Office Supplies|         Art|
|Office Supplies|     Binders|
|     Technology| Accessories|
|Office Supplies|   Fasteners|
|      Furniture|   Bookcases|
|     Technology|      Phones|
|Office Supplies|      Labels|
|     Technology|    Machines|
|      Furniture|      Tables|
|      Furniture| Furnishings|
+---------------+------------+



Creating Category Dimension Table

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

dim_category = (
    new_df_product.select("Category", "Sub_Category")
    .distinct()
    .withColumn("Category_ID", monotonically_increasing_id() + 1)
)

dim_category = dim_category.select("Category_ID", "Category", "Sub_Category")

In [0]:
display(dim_category)

Category_ID Category Sub_Category 1 Office Supplies Appliances 2 Office Supplies Envelopes 3 Furniture Chairs 4 Office Supplies Storage 5 Office Supplies Paper 6 Office Supplies Supplies 7 Technology Copiers 8 Office Supplies Art 9 Office Supplies Binders 10 Technology Accessories 11 Office Supplies Fasteners 12 Furniture Bookcases 13 Technology Phones 14 Office Supplies Labels 15 Technology Machines 16 Furniture Tables 17 Furniture Furnishings

In [0]:
new_df_product = (
    new_df_product.select("Product_ID", "Product_Name", "Category", "Sub_Category")
    .join(dim_category, ["Category", "Sub_Category"], "inner")
    .select("Product_ID", "Product_Name", "Category_ID")
)

In [0]:
display(new_df_product)

Product_ID Product_Name Category_ID FUR-BO-10001798 Bush Somerset Collection Bookcase 12 FUR-CH-10000454 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 3 OFF-LA-10000240 Self-Adhesive Address Labels for Typewriters by Universal 14 FUR-TA-10000577 Bretford CR4500 Series Slim Rectangular Table 16 OFF-ST-10000760 Eldon Fold 'N Roll Cart System 4 FUR-FU-10001487 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 17 OFF-AR-10002833 Newell 322 8 TEC-PH-10002275 Mitel 5320 IP Phone VoIP phone 13 OFF-BI-10003910 DXL Angle-View Binders with Locking Rings by Samsill 9 OFF-AP-10002892 Belkin F5C206VTEL 6 Outlet Surge 1 FUR-TA-10001539 Chromcraft Rectangular Conference Tables 16 TEC-PH-10002033 Konftel 250 ConferenceÂ phoneÂ - Charcoal black 13 OFF-PA-10002365 Xerox 1967 5 OFF-BI-10003656 Fellowes PB200 Plastic Comb Binding Machine 9 OFF-AP-10002311 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 1 OFF-BI-10000756 Storex DuraTech Recycled Plastic Frosted Binders 9 OFF-ST-10004186 "Stur-D-Stor Shelving, Vertical 5-Shelf: 72""H x 36""W x 18 1/2""D" 4 OFF-ST-10000107 Fellowes Super Stor/Drawer 4 OFF-AR-10003056 Newell 341 8 TEC-PH-10001949 Cisco SPA 501G IP Phone 13 OFF-BI-10002215 Wilson Jones Hanging View Binder, White, 1"" 9 OFF-AR-10000246 Newell 318 8 OFF-AP-10001492 Acco Six-Outlet Power Strip, 4' Cord Length 1 FUR-CH-10002774 Global Deluxe Stacking Chair, Gray 3 OFF-BI-10001634 Wilson Jones Active Use Binders 9 TEC-AC-10003027 ImationÂ 8GB Mini TravelDrive USB 2.0Â Flash Drive 10 FUR-BO-10004834 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 12 OFF-BI-10000474 Avery Recycled Flexi-View Covers for Binding Systems 9 FUR-FU-10004848 "Howard Miller 13-3/4"" Diameter Brushed Chrome Round Wall Clock" 17 OFF-EN-10001509 Poly String Tie Envelopes 2 OFF-AR-10004042 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 8 OFF-BI-10001525 "Acco Pressboard Covers with Storage Hooks, 14 7/8"" x 11"" 9 OFF-AR-10001683 Lumber Crayons 8 OFF-PA-10000249 Easy-staple paper 5 TEC-PH-10004977 GE 30524EE4 13 FUR-FU-10003664 Electrix Architect's Clamp-On Swing Arm Lamp, Black 17 OFF-EN-10002986 "#10-4 1/8"" x 9 1/2"" Premium Diagonal Seam Envelopes" 2 FUR-BO-10002545 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 12 FUR-CH-10004218 Global Fabric Manager's Chair, Dark Gray 3 TEC-PH-10000486 Plantronics HL10 Handset Lifter 13 TEC-PH-10004093 Panasonic Kx-TS550 13 OFF-ST-10003479 Eldon Base for stackable storage shelf, platinum 4 OFF-ST-10003282 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 4 TEC-AC-10000171 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 10 OFF-BI-10003291 Wilson Jones Leather-Like Binders with DublLock Round Rings 9 OFF-ST-10001713 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 4 TEC-AC-10002167 ImationÂ 8gb Micro Traveldrive Usb 2.0Â Flash Drive 10 TEC-PH-10003988 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 13 OFF-BI-10004410 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-1/8, 10/Pack 9 OFF-LA-10002762 Avery 485 14 FUR-FU-10001706 Longer-Life Soft White Bulbs 17 FUR-CH-10003061 Global Leather Task Chair, Black 3 OFF-FA-10000304 Advantus Push Pins 11 TEC-PH-10002447 AT&T CL83451 4-Handset Telephone 13 OFF-ST-10000604 Home/Office Personal File Carts 4 OFF-PA-10001569 Xerox 232 5 FUR-CH-10003968 Novimex Turbo Task Chair 3 OFF-PA-10000587 Array Parchment Paper, Assorted Colors 5 OFF-BI-10001460 Plastic Binding Combs 9 OFF-AR-10001868 Prang Dustless Chalk Sticks 8 TEC-AC-10004633 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 3/Pack 10 OFF-BI-10001078 "Acco PRESSTEX Data Binder with Storage Hooks, Dark Blue, 14 7/8"" X 11""" 9 OFF-PA-10003892 Xerox 1943 5 FUR-FU-10000397 Luxo Economy Swing Arm Lamp 17 FUR-CH-10001146 Global Value Mid-Back Manager's Chair, Gray 3 OFF-AR-10002671 Hunt BOSTON Model 1606 High-Volume Electric Pencil

Normalizing Customer Table

In [0]:
display(new_df_customer.select("Country", "Region","State", "City", "Postal_Code").distinct())

Country Region State City Postal_Code United States West Arizona Gilbert 85234 United States West California Los Angeles 90045 United States South Virginia Charlottesville 22901 United States East Maryland Baltimore 21215 United States East Ohio Grove City 43123 United States East New York New York City 10011 United States East New York Niagara Falls 14304 United States Central Minnesota Minneapolis 55407 United States West Washington Seattle 98115 United States Central Texas Austin 78745 United States Central Michigan Jackson 49201 United States West California Manteca 95336 United States East Rhode Island Warwick 2886 United States South Georgia Smyrna 30080 United States South Florida Saint Petersburg 33710 United States East Pennsylvania Philadelphia 19143 United States West Arizona Mesa 85204 United States East New Jersey Bridgeton 8302 United States South North Carolina Gastonia 28052 United States East New York Watertown 13601 United States West California Santa Ana 92704 United States West California San Francisco 94109 United States Central Texas Houston 77036 United States East Ohio Medina 44256 United States East New Jersey New Brunswick 8901 United States Central Indiana La Porte 46350 United States West California Salinas 93905 United States Central Texas San Antonio 78207 United States Central Texas Allen 75002 United States South North Carolina Fayetteville 28314 United States South Virginia Springfield 22153 United States Central Minnesota Eagan 55122 United States East New York New York City 10009 United States East New York Lindenhurst 11757 United States Central Texas Plano 75023 United States West California Pasadena 91104 United States South Alabama Decatur 35601 United States East Maryland Columbia 21044 United States Central Michigan Lincoln Park 48146 United States West Colorado Colorado Springs 80906 United States South Alabama Huntsville 35810 United States West Colorado Denver 80219 United States South Florida Tamarac 33319 United States East Massachusetts Lowell 1852 United States West California Lancaster 93534 United States Central Minnesota Saint Paul 55106 United States Central Missouri Saint Peters 63376 United States East New York Buffalo 14215 United States Central Illinois Chicago 60610 United States East Ohio Akron 44312 United States Central Michigan Detroit 48227 United States South Tennessee Murfreesboro 37130 United States West California San Diego 92105 United States Central Indiana Columbus 47201 United States South Virginia Virginia Beach 23464 United States Central Texas Amarillo 79109 United States South North Carolina Chapel Hill 27514 United States South Kentucky Louisville 40214 United States Central Michigan Trenton 48183 United States Central Texas Grapevine 76051 United States West Arizona Glendale 85301 United States South Tennessee Jackson 38301 United States Central Iowa Des Moines 50315 United States Central Wisconsin Milwaukee 53209 United States South Florida Pembroke Pines 33024 United States East Ohio Kent 44240 United States West California Redlands 92374 United States West Colorado Arvada 80004 United States East New Jersey Hackensack 7601 United States West Colorado Parker 80134 United States West California Escondido 92025 United States East Ohio Dublin 43017 United States Central Texas Houston 77041 United States Central Texas Grand Prairie 75051 United States East New York New York City 10024 United States Central Illinois Aurora 60505 United States Central Texas Tyler 75701 United States West Washington Olympia 98502 United States Central Texas Mcallen 78501 United States South Alabama Montgomery 36116 United States West California Lake Elsinore 92530 United States Central Iowa Burlington 52601 United States West California Whittier 90604 United States West California San Diego 92037 United States West California Vallejo 94591 United States South Georgia Columbus 31907 United States Central Texas Dallas 75217 United States South North Carolina Asheville 28806 U

Creating Address and Customer Segment Dimension Tables

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

dim_address = (
    new_df_customer.select("Country", "Region","State", "City", "Postal_Code")
    .distinct()
    .withColumn("Address_ID", monotonically_increasing_id() + 1)
)

dim_address = dim_address.select("Address_ID", "Country", "Region","State", "City", "Postal_Code")

dim_cust_segment = (
    new_df_customer.select("Segment")
    .distinct()
    .withColumn("Customer_Segment_ID", monotonically_increasing_id() + 1)
)

dim_cust_segment = dim_cust_segment.select("Customer_Segment_ID", "Segment")

In [0]:
display(dim_address)

Address_ID Country Region State City Postal_Code 1 United States West Arizona Gilbert 85234 2 United States West California Los Angeles 90045 3 United States South Virginia Charlottesville 22901 4 United States East Maryland Baltimore 21215 5 United States East Ohio Grove City 43123 6 United States East New York New York City 10011 7 United States East New York Niagara Falls 14304 8 United States Central Minnesota Minneapolis 55407 9 United States West Washington Seattle 98115 10 United States Central Texas Austin 78745 11 United States Central Michigan Jackson 49201 12 United States West California Manteca 95336 13 United States East Rhode Island Warwick 2886 14 United States South Georgia Smyrna 30080 15 United States South Florida Saint Petersburg 33710 16 United States East Pennsylvania Philadelphia 19143 17 United States West Arizona Mesa 85204 18 United States East New Jersey Bridgeton 8302 19 United States South North Carolina Gastonia 28052 20 United States East New York Watertown 13601 21 United States West California Santa Ana 92704 22 United States West California San Francisco 94109 23 United States Central Texas Houston 77036 24 United States East Ohio Medina 44256 25 United States East New Jersey New Brunswick 8901 26 United States Central Indiana La Porte 46350 27 United States West California Salinas 93905 28 United States Central Texas San Antonio 78207 29 United States Central Texas Allen 75002 30 United States South North Carolina Fayetteville 28314 31 United States South Virginia Springfield 22153 32 United States Central Minnesota Eagan 55122 33 United States East New York New York City 10009 34 United States East New York Lindenhurst 11757 35 United States Central Texas Plano 75023 36 United States West California Pasadena 91104 37 United States South Alabama Decatur 35601 38 United States East Maryland Columbia 21044 39 United States Central Michigan Lincoln Park 48146 40 United States West Colorado Colorado Springs 80906 41 United States South Alabama Huntsville 35810 42 United States West Colorado Denver 80219 43 United States South Florida Tamarac 33319 44 United States East Massachusetts Lowell 1852 45 United States West California Lancaster 93534 46 United States Central Minnesota Saint Paul 55106 47 United States Central Missouri Saint Peters 63376 48 United States East New York Buffalo 14215 49 United States Central Illinois Chicago 60610 50 United States East Ohio Akron 44312 51 United States Central Michigan Detroit 48227 52 United States South Tennessee Murfreesboro 37130 53 United States West California San Diego 92105 54 United States Central Indiana Columbus 47201 55 United States South Virginia Virginia Beach 23464 56 United States Central Texas Amarillo 79109 57 United States South North Carolina Chapel Hill 27514 58 United States South Kentucky Louisville 40214 59 United States Central Michigan Trenton 48183 60 United States Central Texas Grapevine 76051 61 United States West Arizona Glendale 85301 62 United States South Tennessee Jackson 38301 63 United States Central Iowa Des Moines 50315 64 United States Central Wisconsin Milwaukee 53209 65 United States South Florida Pembroke Pines 33024 66 United States East Ohio Kent 44240 67 United States West California Redlands 92374 68 United States West Colorado Arvada 80004 69 United States East New Jersey Hackensack 7601 70 United States West Colorado Parker 80134 71 United States West California Escondido 92025 72 United States East Ohio Dublin 43017 73 United States Central Texas Houston 77041 74 United States Central Texas Grand Prairie 75051 75 United States East New York New York City 10024 76 United States Central Illinois Aurora 60505 77 United States Central Texas Tyler 75701 78 United States West Washington Olympia 98502 79 United States Central Texas Mcallen 78501 80 United States South Alabama Montgomery 36116 81 United States West California Lake Elsinore 92530 82 United States Central Iowa Burlington 52601 83 United States West C

In [0]:
display(dim_cust_segment)

Customer_Segment_ID Segment 1 Consumer 2 Home Office 3 Corporate

In [0]:
display(new_df_customer)

Customer_ID Customer_Name Segment Country City State Postal_Code Region Age CG/12520 Claire Gute Consumer United States Henderson Kentucky 42420 South 42 DV/13045 Darrin Van Huff Corporate United States Los Angeles California 90036 West 47 SO/20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South 19 BH/11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West 39 AA/10480 Andrew Allen Consumer United States Concord North Carolina 28027 South 31 IM/15070 Irene Maddox Consumer United States Seattle Washington 98103 West 45 HP/14815 Harold Pawlan Home Office United States Fort Worth Texas 76106 Central 38 PK/19075 Pete Kriz Consumer United States Madison Wisconsin 53711 Central 38 AG/10270 Alejandro Grove Consumer United States West Jordan Utah 84084 West 36 ZD/21925 Zuschuss Donatelli Consumer United States San Francisco California 94109 West 19 KB/16585 Ken Black Corporate United States Fremont Nebraska 68025 Central 29 SF/20065 Sandra Flanagan Consumer United States Philadelphia Pennsylvania 19140 East 45 EB/13870 Emily Burns Consumer United States Orem Utah 84057 West 48 EH/13945 Eric Hoffmann Consumer United States Los Angeles California 90049 West 45 TB/21520 Tracy Blumstein Consumer United States Philadelphia Pennsylvania 19140 East 23 MA/17560 Matt Abelman Home Office United States Houston Texas 77095 Central 26 GH/14485 Gene Hale Corporate United States Richardson Texas 75080 Central 33 SN/20710 Steve Nguyen Home Office United States Houston Texas 77041 Central 22 LC/16930 Linda Cazamias Corporate United States Naperville Illinois 60540 Central 45 RA/19885 Ruben Ausman Corporate United States Los Angeles California 90049 West 32 ES/14080 Erin Smith Corporate United States Melbourne Florida 32935 South 32 ON/18715 Odella Nelson Corporate United States Eagan Minnesota 55122 Central 30 PO/18865 Patrick O'Donnell Consumer United States Westland Michigan 48185 Central 48 LH/16900 Lena Hernandez Consumer United States Dover Delaware 19901 East 40 DP/13000 Darren Powers Consumer United States New Albany Indiana 47150 Central 28 JM/15265 Janet Molinari Corporate United States New York City New York 10024 East 34 TB/21055 Ted Butterfield Consumer United States Troy New York 12180 East 20 KM/16720 Kunst Miller Consumer United States Los Angeles California 90004 West 33 PS/18970 Paul Stevenson Home Office United States Chicago Illinois 60610 Central 29 BS/11590 Brendan Sweed Corporate United States Gilbert Arizona 85234 West 33 KD/16270 Karen Daniels Consumer United States Springfield Virginia 22153 South 39 HM/14980 Henry MacAllister Consumer United States New York City New York 10009 East 39 JE/15745 Joel Eaton Consumer United States Memphis Tennessee 38109 South 20 KB/16600 Ken Brennan Corporate United States Houston Texas 77041 Central 30 SC/20770 Stewart Carmichael Corporate United States Decatur Alabama 35601 South 46 DN/13690 Duane Noonan Consumer United States San Francisco California 94122 West 21 JC/16105 Julie Creighton Corporate United States Durham North Carolina 27707 South 30 CS/12400 Christopher Schild Home Office United States Chicago Illinois 60623 Central 44 PG/18895 Paul Gonzalez Consumer United States Rochester Minnesota 55901 Central 23 GM/14455 Gary Mitchum Home Office United States Houston Texas 77095 Central 41 JS/15685 Jim Sink Corporate United States Los Angeles California 90036 West 31 KB/16315 Karl Braun Consumer United States Minneapolis Minnesota 55407 Central 21 RB/19705 Roger Barcio Home Office United States Portland Oregon 97206 West 39 PN/18775 Parhena Norris Home Office United States New York City New York 10009 East 35 KD/16345 Katherine Ducich Consumer United States San Francisco California 94122 West 35 ER/13855 Elpida Rittenbach Corporate United States Saint Paul Minnesota 55106 Central 20 RB/19465 Rick Bensley Home Office United States Chicago Illinois 60610 Central 32 GZ/14470 Gary Zandusky Consumer United States Rochester Minnesota 55901 Central

In [0]:
new_df_customer = (
    new_df_customer.select("Customer_ID", "Customer_Name", "Segment", "Country", "City", "State","Postal_Code", "Region", "Age")
    .join(dim_address, ["Country", "Region","State", "City", "Postal_Code"], "inner")
    .join(dim_cust_segment, "Segment", "inner")
    .select("Customer_ID", "Customer_Name", "Age", "Customer_Segment_ID","Address_ID")
)

In [0]:
display(new_df_customer)

Customer_ID Customer_Name Age Customer_Segment_ID Address_ID PF/19120 Peter Fuller 46 1 1 AO/10810 Anthony O'Donnell 37 3 2 AS/10090 Adam Shillingsburg 40 1 3 BF/11080 Bart Folk 38 1 4 CK/12595 Clytie Kelty 35 1 5 BS/11365 Bill Shonely 46 3 6 NP/18685 Nora Pelletier 39 2 7 AC/10450 Amy Cox 31 1 8 MH/18025 Michelle Huthwaite 34 1 9 RD/19930 Russell D'Ascenzo 33 1 10 PM/18940 Paul MacIntyre 24 1 11 KF/16285 Karen Ferguson 47 2 12 SS/20140 Saphhira Shifley 38 3 13 PP/18955 Paul Prost 36 2 14 AJ/10795 Anthony Johnson 47 3 15 HD/14785 Harold Dahlen 27 2 16 RW/19540 Rick Wilson 28 3 17 JM/15655 Jim Mitchum 29 3 18 RB/19795 Ross Baird 21 2 19 MA/17995 Michelle Arnett 36 2 20 EK/13795 Eileen Kiefer 24 2 21 VP/21760 Victoria Pisteka 44 3 22 JL/15130 Jack Lebron 34 1 23 VW/21775 Victoria Wilson 25 3 24 SJ/20125 Sanjit Jacobs 23 2 25 DB/13405 Denny Blanton 35 1 26 DK/12835 Damala Kotsonis 31 3 27 JC/15775 John Castell 38 1 28 AW/10840 Anthony Witt 27 1 29 CC/12370 Christopher Conant 28 1 30 JJ/15760 Joel Jenkins 44 2 31 ON/18715 Odella Nelson 30 3 32 DB/13360 Dennis Bolton 31 2 33 MH/17785 Maya Herman 42 3 34 SC/20020 Sam Craven 24 1 35 BF/11005 Barry Franz 21 2 36 EH/14185 Evan Henry 40 1 37 EL/13735 Ed Ludwig 42 2 38 DM/12955 Dario Medina 25 3 39 KL/16555 Kelly Lampkin 40 3 40 FW/14395 Fred Wasserman 23 3 41 EH/14005 Erica Hernandez 35 2 42 AH/10195 Alan Haines 48 3 43 RR/19525 Rick Reed 45 3 44 LT/17110 Liz Thompson 22 1 45 QJ/19255 Quincy Jones 19 3 46 RD/19660 Robert Dilbeck 26 2 47 MG/17695 Maureen Gnade 26 1 48 JD/16015 Joy Daniels 30 1 49 EB/13705 Ed Braxton 35 3 50 SW/20350 Sean Wendt 41 2 51 PJ/18835 Patrick Jones 34 3 52 HW/14935 Helen Wasserman 38 3 53 VF/21715 Vicky Freymann 41 2 54 EM/14200 Evan Minnotte 41 2 55 HG/15025 Hunter Glantz 28 1 56 CB/12535 Claudia Bergmann 40 3 57 SS/20515 Shirley Schmidt 47 2 58 RF/19735 Roland Fjeld 47 1 59 MY/18295 Muhammed Yedwab 26 3 60 GH/14410 Gary Hansen 27 2 61 SH/20635 Stefanie Holloman 30 3 62 BV/11245 Benjamin Venier 40 3 63 TS/21655 Trudy Schmidt 46 1 64 DO/13435 Denny Ordway 37 1 65 RE/19405 Ricardo Emerson 24 1 66 MZ/17515 Mary Zewe 25 3 67 BP/11185 Ben Peterman 32 3 68 TS/21205 Thomas Seio 40 3 69 MY/17380 Maribeth Yedwab 46 3 70 LT/16765 Larry Tron 35 1 71 FM/14215 Filia McAdams 34 3 72 DD/13570 Dorothy Dickinson 47 1 73 SJ/20215 Sarah Jordon 40 1 74 AH/10690 Anna HÃ¤berlin 36 3 75 NR/18550 Nick Radford 44 1 76 CD/11980 Carol Darley 28 1 77 RD/19480 Rick Duston 31 1 78 SG/20890 Susan Gilcrest 48 3 79 RL/19615 Rob Lucas 43 1 80 CD/11920 Carlos Daly 38 1 81 RS/19870 Roy Skaria 36 2 82 LE/16810 Laurel Elliston 24 1 83 EJ/13720 Ed Jacobs 42 1 84 DF/13135 David Flashing 47 1 85 AR/10570 Anemone Ratner 31 1 86 NC/18535 Nick Crebassa 46 3 87 JK/15730 Joe Kamberova 28 1 88 BT/11440 Bobby Trafton 27 1 89 SC/20095 Sanjit Chand 21 1 90 BD/11635 Brian Derr 35 1 91 MP/18175 Mike Pelletier 44 2 92 CM/11815 Candace McMahon 21 3 93 ML/17755 Max Ludwig 39 2 94 JD/15790 John Dryer 23 1 95 AA/10480 Andrew Allen 31 1 96 CK/12325 Christine Kargatis 19 2 97 MC/17605 Matt Connell 42 3 98 RA/19945 Ryan Akin 34 1 99 SU/20665 Stephanie Ulpright 33 2 100 SV/20785 Stewart Visinsky 43 1 101 CJ/11875 Carl Jackson 19 3 102 PO/18865 Patrick O'Donnell 48 1 103 TS/21085 Thais Sissman 45 1 104 HK/14890 Heather Kirkland 29 3 105 JK/15370 Jay Kimmel 47 1 106 DC/13285 Debra Catini 47 1 107 BW/11200 Ben Wallace 32 1 108 KB/16585 Ken Black 29 3 109 BG/11740 Bruce Geld 44 1 110 BE/11455 Brad Eason 45 2 111 AR/10345 Alex Russell 23 3 112 LS/17245 Lynn Smith 36 1 113 NW/18400 Natalie Webber 22 1 114 LR/17035 Lisa Ryan 23 3 115 PH/18790 Patricia Hirasaki 48 2 116 DE/13255 Deanra Eno 42 2 117 AF/10870 Art Ferguson 37 1 118 MC/17635 Matthew Clasen 28 3 119 RH/19555 Ritsa Hightower 22 1 120 KB/16405 Katrina Bavinger 29 2 121 SC/20305 Sean Christensen 32 1 122 BN/11470 Brad Norvell 25 3 123 MC/17275 Marc Crier 36 1 124 DH/13675 Duane Huffman 32 2 125 FC/14245 Frank Carlisle 28 2 126 RD/19585 Rob Dowd 46 1 127 MG/18205 Mitch G

In [0]:
new_df_customer.where(new_df_customer["Customer_Name"] == 'Harold Pawlan').show()

+-----------+-------------+---+-------------------+----------+
|Customer_ID|Customer_Name|Age|Customer_Segment_ID|Address_ID|
+-----------+-------------+---+-------------------+----------+
|   HP/14815|Harold Pawlan| 38|                  2|       135|
+-----------+-------------+---+-------------------+----------+



Normalizing Store Table

In [0]:
display(new_df_store)

Order_ID Order_Date Ship_Date Ship_Mode Customer_ID Product_ID Sales Discount CA-2017-152156 2017-11-08 2017-11-11 Second Class CG/12520 FUR-BO-10001798 3929400.0 0.02 CA-2017-152156 2017-11-08 2017-11-11 Second Class CG/12520 FUR-CH-10000454 1.09791E7 0.01 CA-2017-138688 2017-06-12 2017-06-16 Second Class DV/13045 OFF-LA-10000240 219300.0 0.01 US-2016-108966 2016-10-11 2016-10-18 Standard Class SO/20335 FUR-TA-10000577 1.43636625E7 0.02 US-2016-108966 2016-10-11 2016-10-18 Standard Class SO/20335 OFF-ST-10000760 335520.0 0.03 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 FUR-FU-10001487 732900.0 0.02 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 OFF-AR-10002833 109200.0 0.02 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 TEC-PH-10002275 1.360728E7 0.02 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 OFF-BI-10003910 277560.0 0.02 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 OFF-AP-10002892 1723500.0 0.01 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 FUR-TA-10001539 2.559276E7 0.01 CA-2015-115812 2015-06-09 2015-06-14 Standard Class BH/11710 TEC-PH-10002033 1.367136E7 0.03 CA-2018-114412 2018-04-15 2018-04-20 Standard Class AA/10480 OFF-PA-10002365 233280.0 0.02 CA-2017-161389 2017-12-05 2017-12-10 Standard Class IM/15070 OFF-BI-10003656 6119640.0 0.02 US-2016-118983 2016-11-22 2016-11-26 Standard Class HP/14815 OFF-AP-10002311 1032150.0 0.02 US-2016-118983 2016-11-22 2016-11-26 Standard Class HP/14815 OFF-BI-10000756 38160.0 0.03 CA-2015-105893 2015-11-11 2015-11-18 Standard Class PK/19075 OFF-ST-10004186 9988200.0 0.02 CA-2015-167164 2015-05-13 2015-05-15 Second Class AG/10270 OFF-ST-10000107 832500.0 0.01 CA-2015-143336 2015-08-27 2015-09-01 Second Class ZD/21925 OFF-AR-10003056 128400.0 0.01 CA-2015-143336 2015-08-27 2015-09-01 Second Class ZD/21925 TEC-PH-10001949 3202200.0 0.03 CA-2015-143336 2015-08-27 2015-09-01 Second Class ZD/21925 OFF-BI-10002215 340800.0 0.03 CA-2017-137330 2017-12-09 2017-12-13 Standard Class KB/16585 OFF-AR-10000246 291900.0 0.03 CA-2017-137330 2017-12-09 2017-12-13 Standard Class KB/16585 OFF-AP-10001492 905100.0 0.01 US-2018-156909 2018-07-16 2018-07-18 Second Class SF/20065 FUR-CH-10002774 1070580.0 0.02 CA-2016-106320 2016-09-25 2016-09-30 Standard Class EB/13870 FUR-TA-10000577 1.566945E7 0.02 CA-2017-121755 2017-01-16 2017-01-20 Second Class EH/13945 OFF-BI-10001634 174720.0 0.02 CA-2017-121755 2017-01-16 2017-01-20 Second Class EH/13945 TEC-AC-10003027 1358550.0 0.03 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 FUR-BO-10004834 4.625145E7 0.02 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 OFF-BI-10000474 144270.0 0.02 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 FUR-FU-10004848 1863000.0 0.03 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 OFF-EN-10001509 48960.0 0.02 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 OFF-AR-10004042 1294560.0 0.02 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 OFF-BI-10001525 102870.0 0.01 US-2016-150630 2016-09-17 2016-09-21 Standard Class TB/21520 OFF-AR-10001683 236400.0 0.03 CA-2018-107727 2018-10-19 2018-10-23 Second Class MA/17560 OFF-PA-10000249 442080.0 0.02 CA-2017-117590 2017-12-08 2017-12-10 First Class GH/14485 TEC-PH-10004977 1.646316E7 0.01 CA-2017-117590 2017-12-08 2017-12-10 First Class GH/14485 FUR-FU-10003664 2863800.0 0.01 CA-2016-117415 2016-12-27 2016-12-31 Standard Class SN/20710 OFF-EN-10002986 1699920.0 0.02 CA-2016-117415 2016-12-27 2016-12-31 Standard Class SN/20710 FUR-BO-10002545 7985988.0 0.03 CA-2016-117415 2016-12-27 2016-12-31 Standard Class SN/20710 FUR-CH-10004218 3180870.0 0.02 CA-2016-117415 2016-12-27 2016-12-31 Standard Class SN/20710 TEC-PH-10000486 5567520.0 0.01 CA-2018-120999 2018-09-10 2018-09-15 Standard Class LC/16930 TEC-PH-10004093 2207520.0 0.02 CA-2017-101343 2017-07-17 2017-07-22 Standard Class RA/19885 OFF-ST-10003479 1168200.0 0.03 CA-20

Creating Date Dimension

In [0]:
from pyspark.sql.functions import min, max
min_date = new_df_store.select(min("Order_Date"), min("Ship_Date")).collect()
min_order_date = min_date[0][0]
min_ship_date = min_date[0][1]

max_date = new_df_store.select(max("Order_Date"), max("Ship_Date")).collect()
max_order_date = max_date[0][0]
max_ship_date = max_date[0][1]

start_date = min_order_date if min_order_date < min_ship_date else min_ship_date
end_date = max_order_date if max_order_date > max_ship_date else max_ship_date
print('Start Date: ', start_date)
print('End Date: ', end_date)

Start Date:  2015-01-03
End Date:  2019-01-05


In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import *

dateDimSchema = StructType([
    StructField("date", DateType(), False),
    StructField("year", IntegerType(), False),
    StructField("quarter", IntegerType(), False),
    StructField("month", IntegerType(), False),
    StructField("month_name", StringType(), False),
    StructField("day", IntegerType(), False),
    StructField("day_of_week", IntegerType(), False),
    StructField("day_of_week_name", StringType(), False)
])

dates = spark.sql(
    f"""
    SELECT
        to_date(date_sub(date_add('{start_date}', row_number() OVER (ORDER BY 'a')), 1)) AS date
    FROM
        (SELECT explode(sequence(0, datediff('{end_date}', '{start_date}'))) AS row_num) a
    """
)

dim_date = dates.withColumn("year", F.year("date")) \
    .withColumn("quarter", F.quarter("date")) \
    .withColumn("month", F.month("date")) \
    .withColumn("month_name", F.date_format("date", "MMMM")) \
    .withColumn("day", F.dayofmonth("date")) \
    .withColumn("day_of_week", F.dayofweek("date")) \
    .withColumn("day_of_week_name", F.date_format("date", "EEEE")) \
    .select("date", "year", "quarter", "month", "month_name", "day", "day_of_week", "day_of_week_name") \
    .withColumn("year", F.col("year").cast(IntegerType())) \
    .withColumn("quarter", F.col("quarter").cast(IntegerType())) \
    .withColumn("month", F.col("month").cast(IntegerType())) \
    .withColumn("day", F.col("day").cast(IntegerType())) \
    .withColumn("day_of_week", F.col("day_of_week").cast(IntegerType()))

display(dim_date)

date year quarter month month_name day day_of_week day_of_week_name 2015-01-03 2015 1 1 January 3 7 Saturday 2015-01-04 2015 1 1 January 4 1 Sunday 2015-01-05 2015 1 1 January 5 2 Monday 2015-01-06 2015 1 1 January 6 3 Tuesday 2015-01-07 2015 1 1 January 7 4 Wednesday 2015-01-08 2015 1 1 January 8 5 Thursday 2015-01-09 2015 1 1 January 9 6 Friday 2015-01-10 2015 1 1 January 10 7 Saturday 2015-01-11 2015 1 1 January 11 1 Sunday 2015-01-12 2015 1 1 January 12 2 Monday 2015-01-13 2015 1 1 January 13 3 Tuesday 2015-01-14 2015 1 1 January 14 4 Wednesday 2015-01-15 2015 1 1 January 15 5 Thursday 2015-01-16 2015 1 1 January 16 6 Friday 2015-01-17 2015 1 1 January 17 7 Saturday 2015-01-18 2015 1 1 January 18 1 Sunday 2015-01-19 2015 1 1 January 19 2 Monday 2015-01-20 2015 1 1 January 20 3 Tuesday 2015-01-21 2015 1 1 January 21 4 Wednesday 2015-01-22 2015 1 1 January 22 5 Thursday 2015-01-23 2015 1 1 January 23 6 Friday 2015-01-24 2015 1 1 January 24 7 Saturday 2015-01-25 2015 1 1 January 25 1 Sunday 2015-01-26 2015 1 1 January 26 2 Monday 2015-01-27 2015 1 1 January 27 3 Tuesday 2015-01-28 2015 1 1 January 28 4 Wednesday 2015-01-29 2015 1 1 January 29 5 Thursday 2015-01-30 2015 1 1 January 30 6 Friday 2015-01-31 2015 1 1 January 31 7 Saturday 2015-02-01 2015 1 2 February 1 1 Sunday 2015-02-02 2015 1 2 February 2 2 Monday 2015-02-03 2015 1 2 February 3 3 Tuesday 2015-02-04 2015 1 2 February 4 4 Wednesday 2015-02-05 2015 1 2 February 5 5 Thursday 2015-02-06 2015 1 2 February 6 6 Friday 2015-02-07 2015 1 2 February 7 7 Saturday 2015-02-08 2015 1 2 February 8 1 Sunday 2015-02-09 2015 1 2 February 9 2 Monday 2015-02-10 2015 1 2 February 10 3 Tuesday 2015-02-11 2015 1 2 February 11 4 Wednesday 2015-02-12 2015 1 2 February 12 5 Thursday 2015-02-13 2015 1 2 February 13 6 Friday 2015-02-14 2015 1 2 February 14 7 Saturday 2015-02-15 2015 1 2 February 15 1 Sunday 2015-02-16 2015 1 2 February 16 2 Monday 2015-02-17 2015 1 2 February 17 3 Tuesday 2015-02-18 2015 1 2 February 18 4 Wednesday 2015-02-19 2015 1 2 February 19 5 Thursday 2015-02-20 2015 1 2 February 20 6 Friday 2015-02-21 2015 1 2 February 21 7 Saturday 2015-02-22 2015 1 2 February 22 1 Sunday 2015-02-23 2015 1 2 February 23 2 Monday 2015-02-24 2015 1 2 February 24 3 Tuesday 2015-02-25 2015 1 2 February 25 4 Wednesday 2015-02-26 2015 1 2 February 26 5 Thursday 2015-02-27 2015 1 2 February 27 6 Friday 2015-02-28 2015 1 2 February 28 7 Saturday 2015-03-01 2015 1 3 March 1 1 Sunday 2015-03-02 2015 1 3 March 2 2 Monday 2015-03-03 2015 1 3 March 3 3 Tuesday 2015-03-04 2015 1 3 March 4 4 Wednesday 2015-03-05 2015 1 3 March 5 5 Thursday 2015-03-06 2015 1 3 March 6 6 Friday 2015-03-07 2015 1 3 March 7 7 Saturday 2015-03-08 2015 1 3 March 8 1 Sunday 2015-03-09 2015 1 3 March 9 2 Monday 2015-03-10 2015 1 3 March 10 3 Tuesday 2015-03-11 2015 1 3 March 11 4 Wednesday 2015-03-12 2015 1 3 March 12 5 Thursday 2015-03-13 2015 1 3 March 13 6 Friday 2015-03-14 2015 1 3 March 14 7 Saturday 2015-03-15 2015 1 3 March 15 1 Sunday 2015-03-16 2015 1 3 March 16 2 Monday 2015-03-17 2015 1 3 March 17 3 Tuesday 2015-03-18 2015 1 3 March 18 4 Wednesday 2015-03-19 2015 1 3 March 19 5 Thursday 2015-03-20 2015 1 3 March 20 6 Friday 2015-03-21 2015 1 3 March 21 7 Saturday 2015-03-22 2015 1 3 March 22 1 Sunday 2015-03-23 2015 1 3 March 23 2 Monday 2015-03-24 2015 1 3 March 24 3 Tuesday 2015-03-25 2015 1 3 March 25 4 Wednesday 2015-03-26 2015 1 3 March 26 5 Thursday 2015-03-27 2015 1 3 March 27 6 Friday 2015-03-28 2015 1 3 March 28 7 Saturday 2015-03-29 2015 1 3 March 29 1 Sunday 2015-03-30 2015 1 3 March 30 2 Monday 2015-03-31 2015 1 3 March 31 3 Tuesday 2015-04-01 2015 2 4 April 1 4 Wednesday 2015-04-02 2015 2 4 April 2 5 Thursday 2015-04-03 2015 2 4 April 3 6 Friday 2015-04-04 2015 2 4 April 4 7 Saturday 2015-04-05 2015 2 4 April 5 1 Sunday 2015-04-06 2015 2 4 April 6 2 Monday 2015-04-07 2015 2 4 April 7 3 Tuesday 2015-04-08 2015 2 4 April 8 4 Wednesday 2015-04-09 2015 2 4 April 9 5 Thursday 2015-04-10 2015 2 4 April 

Creating Order Dimension Table

In [0]:
dim_order = new_df_store.select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode").distinct()
display(dim_order)

Order_ID Order_Date Ship_Date Ship_Mode CA-2015-106376 2015-12-05 2015-12-10 Standard Class CA-2015-130092 2015-01-11 2015-01-14 First Class CA-2018-133235 2018-08-01 2018-08-04 First Class CA-2017-159212 2017-11-01 2017-11-05 Standard Class CA-2017-106530 2017-05-08 2017-05-08 Same Day CA-2017-140501 2017-06-23 2017-06-28 Standard Class CA-2018-116225 2018-11-05 2018-11-09 Standard Class CA-2017-164735 2017-04-14 2017-04-19 Second Class CA-2018-118773 2018-02-09 2018-02-14 Standard Class US-2016-163783 2016-12-27 2017-01-01 Standard Class CA-2015-142314 2015-12-23 2015-12-28 Standard Class CA-2015-166863 2015-06-20 2015-06-24 Standard Class CA-2016-129896 2016-06-15 2016-06-20 Standard Class CA-2018-112333 2018-04-08 2018-04-14 Standard Class CA-2016-161998 2016-05-01 2016-05-05 Standard Class US-2015-130358 2015-06-23 2015-06-26 First Class US-2018-135230 2018-09-01 2018-09-07 Standard Class CA-2016-142202 2016-09-18 2016-09-23 Second Class CA-2018-134152 2018-05-27 2018-05-31 Standard Class CA-2017-154662 2017-06-09 2017-06-16 Standard Class CA-2015-166891 2015-10-04 2015-10-06 First Class CA-2016-102806 2016-05-21 2016-05-28 Standard Class CA-2016-123113 2016-11-23 2016-11-27 Second Class CA-2018-163209 2018-05-03 2018-05-07 Standard Class CA-2018-141705 2018-10-24 2018-10-26 First Class CA-2015-163650 2015-09-23 2015-09-25 First Class CA-2017-113243 2017-06-10 2017-06-15 Standard Class CA-2015-134313 2015-11-01 2015-11-07 Standard Class CA-2015-157623 2015-03-14 2015-03-18 Standard Class CA-2017-105963 2017-11-15 2017-11-22 Standard Class CA-2015-106572 2015-09-05 2015-09-10 Standard Class CA-2016-139850 2016-06-12 2016-06-17 Standard Class CA-2018-113418 2018-10-01 2018-10-03 First Class US-2015-121734 2015-04-11 2015-04-16 Standard Class CA-2015-135993 2015-05-28 2015-06-02 Standard Class CA-2018-150602 2018-02-09 2018-02-14 Second Class CA-2015-102652 2015-04-06 2015-04-12 Standard Class CA-2017-165561 2017-11-24 2017-11-28 Standard Class CA-2018-162880 2018-12-25 2018-12-29 Standard Class CA-2015-150581 2015-04-08 2015-04-12 Standard Class US-2018-141677 2018-03-26 2018-03-30 Standard Class CA-2017-152457 2017-09-12 2017-09-18 Standard Class CA-2018-115448 2018-11-11 2018-11-14 First Class CA-2016-109113 2016-12-19 2016-12-23 Standard Class CA-2018-124716 2018-03-27 2018-03-31 Standard Class CA-2018-147354 2018-03-09 2018-03-13 Standard Class CA-2017-146437 2017-01-28 2017-02-01 Second Class CA-2018-156622 2018-11-23 2018-11-26 First Class CA-2016-162950 2016-06-28 2016-07-03 Second Class US-2018-120908 2018-09-30 2018-10-02 First Class CA-2018-119004 2018-11-23 2018-11-28 Standard Class US-2018-100930 2018-04-07 2018-04-12 Standard Class CA-2018-163020 2018-09-15 2018-09-19 Standard Class CA-2015-162775 2015-01-13 2015-01-15 Second Class CA-2015-144407 2015-09-09 2015-09-15 Standard Class CA-2018-150959 2018-11-11 2018-11-13 First Class CA-2017-121034 2017-08-08 2017-08-10 Second Class CA-2017-155187 2017-09-24 2017-09-26 Second Class CA-2018-131618 2018-06-17 2018-06-20 First Class CA-2016-152527 2016-10-17 2016-10-17 Same Day CA-2018-114258 2018-11-05 2018-11-10 Second Class CA-2017-152555 2017-03-29 2017-04-02 Second Class CA-2015-166954 2015-04-25 2015-04-30 Standard Class US-2018-149510 2018-12-03 2018-12-10 Standard Class CA-2016-159863 2016-09-04 2016-09-07 Second Class CA-2018-158883 2018-06-02 2018-06-03 Same Day US-2016-141684 2016-06-29 2016-07-04 Standard Class CA-2016-105571 2016-11-07 2016-11-11 Standard Class CA-2016-130365 2016-04-25 2016-04-29 Standard Class CA-2018-155159 2018-11-25 2018-11-29 Second Class CA-2015-124737 2015-08-23 2015-08-27 Standard Class US-2018-123834 2018-07-21 2018-07-25 Standard Class CA-2018-109393 2018-06-30 2018-07-02 Second Class CA-2016-151722 2016-10-05 2016-10-09 Standard Class CA-2016-134117 2016-12-17 2016-12-19 Second Class CA-2016-102778 2016-11-21 2016-11-24 First Class CA-2015-114321 2015-08-20 2015-08-25 Standard Class US-2015-106992 2015-09-19 2015-09-21 Second

In [0]:
dim_order = (
    dim_order.select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode")
    .join(dim_date, dim_order["Order_Date"] == dim_date["date"], "inner")
    .select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode")
)

dim_order = (
    dim_order.select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode")
    .join(dim_date, dim_order["Ship_Date"] == dim_date["date"], "inner")
    .select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode")
)
display(dim_order)

Order_ID Order_Date Ship_Date Ship_Mode CA-2015-106376 2015-12-05 2015-12-10 Standard Class CA-2015-130092 2015-01-11 2015-01-14 First Class CA-2018-133235 2018-08-01 2018-08-04 First Class CA-2017-159212 2017-11-01 2017-11-05 Standard Class CA-2017-106530 2017-05-08 2017-05-08 Same Day CA-2017-140501 2017-06-23 2017-06-28 Standard Class CA-2018-116225 2018-11-05 2018-11-09 Standard Class CA-2017-164735 2017-04-14 2017-04-19 Second Class CA-2018-118773 2018-02-09 2018-02-14 Standard Class US-2016-163783 2016-12-27 2017-01-01 Standard Class CA-2015-142314 2015-12-23 2015-12-28 Standard Class CA-2015-166863 2015-06-20 2015-06-24 Standard Class CA-2016-129896 2016-06-15 2016-06-20 Standard Class CA-2018-112333 2018-04-08 2018-04-14 Standard Class CA-2016-161998 2016-05-01 2016-05-05 Standard Class US-2015-130358 2015-06-23 2015-06-26 First Class US-2018-135230 2018-09-01 2018-09-07 Standard Class CA-2016-142202 2016-09-18 2016-09-23 Second Class CA-2018-134152 2018-05-27 2018-05-31 Standard Class CA-2017-154662 2017-06-09 2017-06-16 Standard Class CA-2015-166891 2015-10-04 2015-10-06 First Class CA-2016-102806 2016-05-21 2016-05-28 Standard Class CA-2016-123113 2016-11-23 2016-11-27 Second Class CA-2018-163209 2018-05-03 2018-05-07 Standard Class CA-2018-141705 2018-10-24 2018-10-26 First Class CA-2015-163650 2015-09-23 2015-09-25 First Class CA-2017-113243 2017-06-10 2017-06-15 Standard Class CA-2015-134313 2015-11-01 2015-11-07 Standard Class CA-2015-157623 2015-03-14 2015-03-18 Standard Class CA-2017-105963 2017-11-15 2017-11-22 Standard Class CA-2015-106572 2015-09-05 2015-09-10 Standard Class CA-2016-139850 2016-06-12 2016-06-17 Standard Class CA-2018-113418 2018-10-01 2018-10-03 First Class US-2015-121734 2015-04-11 2015-04-16 Standard Class CA-2015-135993 2015-05-28 2015-06-02 Standard Class CA-2018-150602 2018-02-09 2018-02-14 Second Class CA-2015-102652 2015-04-06 2015-04-12 Standard Class CA-2017-165561 2017-11-24 2017-11-28 Standard Class CA-2018-162880 2018-12-25 2018-12-29 Standard Class CA-2015-150581 2015-04-08 2015-04-12 Standard Class US-2018-141677 2018-03-26 2018-03-30 Standard Class CA-2017-152457 2017-09-12 2017-09-18 Standard Class CA-2018-115448 2018-11-11 2018-11-14 First Class CA-2016-109113 2016-12-19 2016-12-23 Standard Class CA-2018-124716 2018-03-27 2018-03-31 Standard Class CA-2018-147354 2018-03-09 2018-03-13 Standard Class CA-2017-146437 2017-01-28 2017-02-01 Second Class CA-2018-156622 2018-11-23 2018-11-26 First Class CA-2016-162950 2016-06-28 2016-07-03 Second Class US-2018-120908 2018-09-30 2018-10-02 First Class CA-2018-119004 2018-11-23 2018-11-28 Standard Class US-2018-100930 2018-04-07 2018-04-12 Standard Class CA-2018-163020 2018-09-15 2018-09-19 Standard Class CA-2015-162775 2015-01-13 2015-01-15 Second Class CA-2015-144407 2015-09-09 2015-09-15 Standard Class CA-2018-150959 2018-11-11 2018-11-13 First Class CA-2017-121034 2017-08-08 2017-08-10 Second Class CA-2017-155187 2017-09-24 2017-09-26 Second Class CA-2018-131618 2018-06-17 2018-06-20 First Class CA-2016-152527 2016-10-17 2016-10-17 Same Day CA-2018-114258 2018-11-05 2018-11-10 Second Class CA-2017-152555 2017-03-29 2017-04-02 Second Class CA-2015-166954 2015-04-25 2015-04-30 Standard Class US-2018-149510 2018-12-03 2018-12-10 Standard Class CA-2016-159863 2016-09-04 2016-09-07 Second Class CA-2018-158883 2018-06-02 2018-06-03 Same Day US-2016-141684 2016-06-29 2016-07-04 Standard Class CA-2016-105571 2016-11-07 2016-11-11 Standard Class CA-2016-130365 2016-04-25 2016-04-29 Standard Class CA-2018-155159 2018-11-25 2018-11-29 Second Class CA-2015-124737 2015-08-23 2015-08-27 Standard Class US-2018-123834 2018-07-21 2018-07-25 Standard Class CA-2018-109393 2018-06-30 2018-07-02 Second Class CA-2016-151722 2016-10-05 2016-10-09 Standard Class CA-2016-134117 2016-12-17 2016-12-19 Second Class CA-2016-102778 2016-11-21 2016-11-24 First Class CA-2015-114321 2015-08-20 2015-08-25 Standard Class US-2015-106992 2015-09-19 2015-09-21 Second

In [0]:
new_df_store = (
    new_df_store.select("Order_ID", "Order_Date", "Ship_Date", "Ship_Mode", "Customer_ID", "Product_ID", "Sales", "Discount")
    .join(dim_order, "Order_ID", "inner")
    .select("Order_ID", "Customer_ID", "Product_ID", "Sales", "Discount")
)
display(new_df_store)

Order_ID Customer_ID Product_ID Sales Discount CA-2015-106376 BS/11590 TEC-PH-10002726 2519520.0 0.03 CA-2015-130092 SV/20365 FUR-FU-10000010 149100.0 0.03 CA-2018-133235 LH/16750 TEC-PH-10002660 4079400.0 0.03 CA-2017-159212 KM/16375 OFF-EN-10002230 3776850.0 0.02 CA-2017-106530 CL/12565 TEC-AC-10001465 871680.0 0.01 CA-2017-140501 IM/15070 OFF-FA-10004076 59400.0 0.01 CA-2018-116225 SV/20935 TEC-AC-10001432 5861250.0 0.01 CA-2017-164735 TB/21400 OFF-ST-10001558 1218000.0 0.02 CA-2018-118773 TP/21415 OFF-AP-10000055 194880.0 0.02 US-2016-163783 DR/12940 OFF-ST-10002957 190080.0 0.02 CA-2015-142314 SF/20200 OFF-AP-10002350 3108600.0 0.03 CA-2015-166863 SC/20020 OFF-ST-10004123 7642320.0 0.01 CA-2016-129896 PF/19120 FUR-FU-10002396 603840.0 0.02 CA-2018-112333 KF/16285 OFF-AP-10001962 629250.0 0.03 CA-2016-161998 DB/13120 OFF-AR-10004022 2590560.0 0.01 US-2015-130358 DL/13330 OFF-SU-10002522 46560.0 0.02 US-2018-135230 CK/12325 OFF-AR-10001166 113700.0 0.03 CA-2016-142202 JR/16210 TEC-AC-10003198 1.07568E7 0.02 CA-2018-134152 RP/19855 OFF-AR-10004062 471600.0 0.02 CA-2017-154662 BF/11215 FUR-TA-10001771 1.03941E7 0.01 CA-2015-166891 CC/12220 FUR-CH-10003298 8841150.0 0.03 CA-2016-102806 HG/14965 OFF-BI-10001597 368820.0 0.03 CA-2016-123113 AT/10735 OFF-AR-10004999 269100.0 0.02 CA-2018-163209 MK/18160 OFF-AR-10003651 344400.0 0.01 CA-2018-141705 PO/18850 FUR-TA-10004607 7761075.0 0.03 CA-2015-163650 TT/21220 OFF-BI-10004965 517500.0 0.01 CA-2017-113243 OT/18730 OFF-PA-10003441 486000.0 0.03 CA-2015-134313 RA/19915 TEC-PH-10001795 2.975952E7 0.02 CA-2015-157623 DK/13225 OFF-AR-10003723 50700.0 0.03 CA-2017-105963 SC/20770 TEC-AC-10003832 1490850.0 0.02 CA-2015-106572 NP/18700 OFF-ST-10000585 3964800.0 0.03 CA-2016-139850 GB/14575 FUR-FU-10003623 649440.0 0.03 CA-2018-113418 CM/12655 TEC-MA-10002428 2.557335E7 0.03 US-2015-121734 SE/20110 OFF-BI-10004817 143760.0 0.02 CA-2015-135993 PJ/18835 TEC-AC-10004877 414000.0 0.02 CA-2018-150602 ML/17395 FUR-FU-10003142 316800.0 0.03 CA-2015-102652 AY/10555 OFF-PA-10001977 832200.0 0.03 CA-2017-165561 CR/12580 OFF-SU-10004782 380250.0 0.03 CA-2018-162880 GD/14590 OFF-BI-10003314 57840.0 0.02 CA-2015-150581 NM/18445 TEC-AC-10001908 5999400.0 0.02 US-2018-141677 HK/14890 OFF-ST-10000344 483480.0 0.03 CA-2017-152457 SC/20695 OFF-PA-10003790 1027800.0 0.03 CA-2018-115448 MH/18025 FUR-FU-10004090 1333800.0 0.01 CA-2016-109113 EK/13795 TEC-AC-10004761 382320.0 0.02 CA-2018-124716 BD/11560 OFF-PA-10000859 179100.0 0.01 CA-2018-147354 KB/16315 OFF-BI-10003910 462600.0 0.01 CA-2017-146437 HG/14965 OFF-AR-10000588 595200.0 0.03 CA-2018-156622 JP/15460 OFF-BI-10003707 91560.0 0.03 CA-2016-162950 DW/13585 FUR-BO-10001918 7244100.0 0.03 US-2018-120908 BF/10975 OFF-LA-10004677 309960.0 0.02 CA-2018-119004 JM/15250 OFF-AR-10000390 49560.0 0.03 US-2018-100930 CS/12400 TEC-AC-10003832 9269640.0 0.02 CA-2018-163020 MO/17800 FUR-FU-10000221 533400.0 0.01 CA-2015-162775 CS/12250 OFF-ST-10000025 8588700.0 0.03 CA-2015-144407 MS/17365 OFF-LA-10003923 1554000.0 0.03 CA-2018-150959 TD/20995 OFF-BI-10001510 275040.0 0.01 CA-2017-121034 JF/15565 OFF-PA-10001994 809280.0 0.02 CA-2017-155187 LA/16780 OFF-PA-10000380 625500.0 0.01 CA-2018-131618 LS/17200 OFF-BI-10001294 140400.0 0.02 CA-2016-152527 CM/12190 OFF-ST-10003479 1168200.0 0.02 CA-2018-114258 EM/13825 TEC-PH-10003012 7391520.0 0.02 CA-2017-152555 ME/17320 TEC-PH-10001254 1.219104E7 0.03 CA-2015-166954 BT/11305 FUR-CH-10003973 2.23056E7 0.02 US-2018-149510 MC/17575 OFF-PA-10001892 366720.0 0.03 CA-2016-159863 DS/13180 TEC-AC-10000109 2015640.0 0.03 CA-2018-158883 CS/11860 OFF-PA-10004733 380160.0 0.01 US-2016-141684 MM/18055 OFF-PA-10002870 374400.0 0.02 CA-2016-105571 CP/12340 OFF-BI-10001359 2.0182275E7 0.02 CA-2016-130365 ZC/21910 FUR-CH-10003535 1920870.0 0.03 CA-2018-155159 DL/13315 OFF-PA-10003724 733050.0 0.03 CA-2015-124737 AP/10915 OFF-PA-10001125 3345840.0 0.02 US-2018-123834 GM/14500 FUR-TA-10001676 1866060.0 0.01 CA-2018-109393 JC/15775 FUR-BO-100

In [0]:
display(new_df_customer.head(5))
display(dim_address.head(5))
display(dim_cust_segment.head(5))
display(new_df_product.head(5))
display(dim_category.head(5))
display(new_df_store.head(5))
display(dim_order.head(5))
display(dim_date.head(5))

Customer_ID Customer_Name Age Customer_Segment_ID Address_ID PF/19120 Peter Fuller 46 1 1 AO/10810 Anthony O'Donnell 37 3 2 AS/10090 Adam Shillingsburg 40 1 3 BF/11080 Bart Folk 38 1 4 CK/12595 Clytie Kelty 35 1 5

Address_ID Country Region State City Postal_Code 1 United States West Arizona Gilbert 85234 2 United States West California Los Angeles 90045 3 United States South Virginia Charlottesville 22901 4 United States East Maryland Baltimore 21215 5 United States East Ohio Grove City 43123

Customer_Segment_ID Segment 1 Consumer 2 Home Office 3 Corporate

Product_ID Product_Name Category_ID FUR-BO-10001798 Bush Somerset Collection Bookcase 12 FUR-CH-10000454 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 3 OFF-LA-10000240 Self-Adhesive Address Labels for Typewriters by Universal 14 FUR-TA-10000577 Bretford CR4500 Series Slim Rectangular Table 16 OFF-ST-10000760 Eldon Fold 'N Roll Cart System 4

Category_ID Category Sub_Category 1 Office Supplies Appliances 2 Office Supplies Envelopes 3 Furniture Chairs 4 Office Supplies Storage 5 Office Supplies Paper

Order_ID Customer_ID Product_ID Sales Discount CA-2015-106376 BS/11590 TEC-PH-10002726 2519520.0 0.03 CA-2015-130092 SV/20365 FUR-FU-10000010 149100.0 0.03 CA-2018-133235 LH/16750 TEC-PH-10002660 4079400.0 0.03 CA-2017-159212 KM/16375 OFF-EN-10002230 3776850.0 0.02 CA-2017-106530 CL/12565 TEC-AC-10001465 871680.0 0.01

Order_ID Order_Date Ship_Date Ship_Mode CA-2015-106376 2015-12-05 2015-12-10 Standard Class CA-2015-130092 2015-01-11 2015-01-14 First Class CA-2018-133235 2018-08-01 2018-08-04 First Class CA-2017-159212 2017-11-01 2017-11-05 Standard Class CA-2017-106530 2017-05-08 2017-05-08 Same Day

date year quarter month month_name day day_of_week day_of_week_name 2015-01-03 2015 1 1 January 3 7 Saturday 2015-01-04 2015 1 1 January 4 1 Sunday 2015-01-05 2015 1 1 January 5 2 Monday 2015-01-06 2015 1 1 January 6 3 Tuesday 2015-01-07 2015 1 1 January 7 4 Wednesday

Saving Data in Gold Container

In [0]:
dfs = [new_df_customer, dim_address, dim_cust_segment, new_df_product, dim_category, new_df_store, dim_order, dim_date]
df_names = ["customer", "address", "customer_segment", "product", "product_category", "sales_detail", "order_detail", "date"]

for i, df in enumerate(dfs, start=1):
  output_path = '/mnt/gold/' + df_names[i-1] + '/'
  df.write.format('delta').mode("overwrite").save(output_path)